In [1]:
import pyscenic
print(pyscenic.__version__)

0.12.1


In [2]:
import dask
print(dask.__version__)

2024.2.1


In [3]:
import numpy as np
import pandas as pd
!pip install scanpy
import scanpy as sc
!pip install igraph
import igraph

import anndata
from scipy import io
from scipy.sparse import coo_matrix, csr_matrix
import os

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com


In [4]:
import os
import glob
import pickle

In [5]:
from dask.diagnostics import ProgressBar
from arboreto.utils import load_tf_names
from arboreto.algo import grnboost2
from ctxcore.rnkdb import FeatherRankingDatabase as RankingDatabase
from pyscenic.utils import modules_from_adjacencies, load_motifs
from pyscenic.prune import prune2df, df2regulons
from pyscenic.aucell import aucell
import seaborn as sns

In [6]:
ex_matrix = pd.read_csv("/home/shruti/Documents/shruti/pySCENIC/beta2_HFD/expression_matrix_beta2_HFD.txt", sep='\t', header=0, index_col=0).T

In [7]:
ex_matrix.shape

(16666, 17576)

In [8]:
tf_names = load_tf_names("/home/shruti/Documents/shruti/pySCENIC/allTFs_mm.txt")

In [9]:
import os
import glob

# Set the path to the directory containing your feather files
DATABASES_GLOB = r"/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/*.feather"  # Assuming the files have a .feather extension

# Use glob to find all matching files
db_fnames = glob.glob(DATABASES_GLOB)

# Debugging: Print what glob returns to check if the files are being found
print("Files found:", db_fnames)

# Define the function to extract the base name without extension
def name(fname):
    return os.path.splitext(os.path.basename(fname))[0]

# Create instances of FeatherRankingDatabase for each file found
dbs = [RankingDatabase(fname=fname, name=name(fname)) for fname in db_fnames]

# Output the list of databases
print(dbs)

Files found: ['/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/mm9-500bp-upstream-10species.mc9nr.genes_vs_motifs.rankings.feather', '/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/mm9-tss-centered-10kb-10species.mc9nr.genes_vs_motifs.rankings.feather', '/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/mm9-500bp-upstream-7species.mc9nr.genes_vs_motifs.rankings.feather', '/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/mm9-tss-centered-10kb-7species.mc9nr.genes_vs_motifs.rankings.feather', '/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/mm9-tss-centered-5kb-7species.mc9nr.genes_vs_motifs.rankings.feather', '/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/mm9-tss-centered-5kb-10species.mc9nr.genes_vs_motifs.rankings.feather']
[FeatherRankingDatabase(name="mm9-500bp-upstream-10species.mc9nr.genes_vs_motifs.rankings"), FeatherRankingDatabase(name="mm9-tss-centered-10kb-10species.mc9nr.genes_vs_motifs.rankings"), Feath

In [10]:
wdir = '/home/shruti/Documents/shruti/pySCENIC/beta2_HFD'
os.chdir(wdir)

In [11]:
ex_matrix.head()

0610005C13Rik  0610009B22Rik  0610009O20Rik  \
HFD-8W-1R_AAACCCAAGGTTCACT-1            0.0            0.0            0.0   
HFD-8W-1R_AAAGTGACACCAGCTG-1            0.0            0.0            0.0   
HFD-8W-1R_AACAACCCATCCTCAC-1            0.0            0.0            0.0   
HFD-8W-1R_AACAAGAGTGATACCT-1            0.0            0.0            0.0   
HFD-8W-1R_AACAAGATCTCTCTAA-1            0.0            0.0            0.0   

                              0610010F05Rik  0610010K14Rik  0610012G03Rik  \
HFD-8W-1R_AAACCCAAGGTTCACT-1            0.0            0.0            0.0   
HFD-8W-1R_AAAGTGACACCAGCTG-1            0.0            0.0            0.0   
HFD-8W-1R_AACAACCCATCCTCAC-1            0.0            0.0            0.0   
HFD-8W-1R_AACAAGAGTGATACCT-1            0.0            0.0            0.0   
HFD-8W-1R_AACAAGATCTCTCTAA-1            0.0            0.0            0.0   

                              0610025J13Rik  0610030E20Rik  0610037L13Rik  \
HFD-8W-1R_AAACCCAAGGTTCACT-1            0.0            0.0            0.0   
HFD-8W-1R_AAAGTGACACCAGCTG-1            0.0            0.0            0.0   
HFD-8W-1R_AACAACCCATCCTCAC-1            0.0            0.0            0.0   
HFD-8W-1R_AACAAGAGTGATACCT-1            0.0            0.0            0.0   
HFD-8W-1R_AACAAGATCTCTCTAA-1            0.0            0.0            0.0   

                              0610038B21Rik  ...  Wnt6  Xpnpep2  Zcchc13  \
HFD-8W-1R_AAACCCAAGGTTCACT-1            0.0  ...   0.0      0.0      0.0   
HFD-8W-1R_AAAGTGACACCAGCTG-1            0.0  ...   0.0      0.0      0.0   
HFD-8W-1R_AACAACCCATCCTCAC-1            0.0  ...   0.0      0.0      0.0   
HFD-8W-1R_AACAAGAGTGATACCT-1            0.0  ...   0.0      0.0      0.0   
HFD-8W-1R_AACAAGATCTCTCTAA-1            0.0  ...   0.0      0.0      0.0   

                              Zfp385c  Zfp536  Zfp711  Zfp831  Zfp981  Zfp985  \
HFD-8W-1R_AAACCCAAGGTTCACT-1      0.0     0.0     0.0     0.0     0.0     0.0   
HFD-8W-1R_AAAGTGACACCAGCTG-1      0.0     0.0     0.0     0.0     0.0     0.0   
HFD-8W-1R_AACAACCCATCCTCAC-1      0.0     0.0     0.0     0.0     0.0     0.0   
HFD-8W-1R_AACAAGAGTGATACCT-1      0.0     0.0     0.0     0.0     0.0     0.0   
HFD-8W-1R_AACAAGATCTCTCTAA-1      0.0     0.0     0.0     0.0     0.0     0.0   

                              Zpld1  
HFD-8W-1R_AAACCCAAGGTTCACT-1    0.0  
HFD-8W-1R_AAAGTGACACCAGCTG-1    0.0  
HFD-8W-1R_AACAACCCATCCTCAC-1    0.0  
HFD-8W-1R_AACAAGAGTGATACCT-1    0.0  
HFD-8W-1R_AACAAGATCTCTCTAA-1    0.0  

[5 rows x 17576 columns]

In [12]:
!pip install dask-expr==0.5.3 distributed==2024.2.1

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com


In [13]:
from dask import delayed
print(type(delayed(ex_matrix)))

<class 'dask.delayed.DelayedLeaf'>


In [14]:
adjancencies = grnboost2(expression_data=ex_matrix, tf_names=tf_names, verbose=True)

preparing dask client
parsing input
creating dask graph
12 partitions
computing dask graph


/home/shruti/anaconda3/envs/attempt_b/lib/python3.10/site-packages/distributed/client.py:3169: UserWarning: Sending large graph of size 2.09 GiB.
This may cause some slowdown.
Consider scattering data ahead of time and using futures.
  warnings.warn(


shutting down client and local cluster
finished


In [15]:
adjancencies.head()

TF  target  importance
772  Rps10   Rps18   20.480819
69   Batf3    Cybb   18.534801
772  Rps10   Cox8a   17.171014
772  Rps10   Parvg   16.052612
779  Runx3  H2-Ab1   15.261377

In [16]:
adjancencies.to_csv("ADJACENCIES_FNAME", index=False, sep='\t')
adjancencies.to_csv("ADJACENCIES_FNAME.csv", index=False)

In [17]:
modules = list(modules_from_adjacencies(adjancencies, ex_matrix))


2024-12-10 13:25:39,098 - pyscenic.utils - INFO - Calculating Pearson correlations.

2024-12-10 13:25:41,420 - pyscenic.utils - WARNING - Note on correlation calculation: the default behaviour for calculating the correlations has changed after pySCENIC verion 0.9.16. Previously, the default was to calculate the correlation between a TF and target gene using only cells with non-zero expression values (mask_dropouts=True). The current default is now to use all cells to match the behavior of the R verision of SCENIC. The original settings can be retained by setting 'rho_mask_dropouts=True' in the modules_from_adjacencies function, or '--mask_dropouts' from the CLI.
	Dropout masking is currently set to [False].

2024-12-10 13:26:03,544 - pyscenic.utils - INFO - Creating modules.


In [18]:
with open("MODULES_FNAME", 'wb') as f:
    pickle.dump(modules, f)

In [19]:
MOTIF_ANNOTATIONS_FNAME = "/home/shruti/Documents/shruti/pySCENIC/motifs-v9-nr.mgi-m0.001-o0.0.tbl"

In [ ]:
df = prune2df(dbs, modules, MOTIF_ANNOTATIONS_FNAME)


2024-12-10 17:31:21,403 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Exo5 could be mapped to mm9-tss-centered-10kb-10species.mc9nr.genes_vs_motifs.rankings. Skipping this module.

2024-12-10 17:31:21,532 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Exosc3 could be mapped to mm9-tss-centered-10kb-10species.mc9nr.genes_vs_motifs.rankings. Skipping this module.

2024-12-10 17:31:22,576 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Gmeb1 could be mapped to mm9-tss-centered-10kb-10species.mc9nr.genes_vs_motifs.rankings. Skipping this module.

2024-12-10 17:31:22,702 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Gmeb2 could be mapped to mm9-tss-centered-10kb-10species.mc9nr.genes_vs_motifs.rankings. Skipping this module.

2024-12-10 17:31:22,819 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Got1 could be mapped to mm9-tss-centered-10kb-10species.